# EDA?
# Geographies & Demographics Consolidation
* Folium mapping

In [1]:
import os                       # For working in different directories
import numpy as np              # Data Libraries
import pandas as pd             # Data Libraries
import matplotlib.pyplot as plt # Visualization Library
import seaborn as sns           # Visualization Library
import folium                   # Visualization Library
from folium.features import GeoJsonTooltip    # Visualization Library
import branca.colormap as cm
import geopandas as gpd         # geospatial library 
import yaml                     # working w/ config file
from importnb import imports    # load other Jupyter Notebooks inside of this notebook
import pickle

### Merge Selected DP variables w/ MSA Geometry to arrive at `Place` demographics w/ geometry
* result is 2021 ACS 5-year demographics for places w/in Denver-Lakewood-Aurora MSA

In [2]:
def load_census_bureau_api_key():
    """Function to load my API key for the Census Bureaus API w/out explicitily providing it."""
    os.chdir('/home/jcorley60/Documents/project_portfolio/DenverBreweries/data/')
    with open('config.yaml', 'r') as file:
        file_contents = yaml.safe_load(file)
    
    return file_contents['api_key'] 


api_key = load_census_bureau_api_key()

### Load GeoPandas GeoDataFrame for MSA Places

In [3]:
os.chdir(
    '/home/jcorley60/Documents/project_portfolio/DenverBreweries/data/US Census Bureau/American Community Survey'
)
gdf_msa_places = pd.read_pickle('gdf_msa_places.pkl')
gdf_msa_places.drop('NAME', axis=1, inplace=True)
gdf_msa_places

GEO_ID              NAMELSAD     ALAND   AWATER   
8    1600000US0824950             Erie town  53222659   260609  \
16   1600000US0850026  Meridian Village CDP   1319424        0   
21   1600000US0869480      Shaw Heights CDP   1814251     2011   
32   1600000US0852350    Mountain View town    240817        0   
39   1600000US0812815       Centennial city  77035924   379304   
..                ...                   ...       ...      ...   
460  1600000US0816495    Commerce City city  94313381  1035683   
461  1600000US0809280       Broomfield city  85386685  1502572   
464  1600000US0842495         Lakeside town    485965   157267   
470  1600000US0830340         Glendale city   1471186     5724   
477  1600000US0850012          Meridian CDP   6636506        0   

                                              geometry  
8    POLYGON ((-105.10469 40.01455, -105.10380 40.0...  
16   POLYGON ((-104.83001 39.52793, -104.82992 39.5...  
21   POLYGON ((-105.05042 39.86008, -105.04054 39.8...  
32   POLYGON ((-105.06019 39.77661, -105.05325 39.7...  
39   MULTIPOLYGON (((-104.97913 39.56942, -104.9769...  
..                                                 ...  
460  MULTIPOLYGON (((-104.67805 39.91401, -104.6591...  
461  MULTIPOLYGON (((-105.10667 39.95783, -105.1073...  
464  POLYGON ((-105.06266 39.78385, -105.05318 39.7...  
470  POLYGON ((-104.94074 39.70634, -104.94068 39.7...  
477  MULTIPOLYGON (((-104.85366 39.53279, -104.8536...  

[61 rows x 5 columns]

### Load Pandas dataframe for Colorado `Place` Demographics

In [4]:
df_demographics = pd.read_pickle('colorado_place_demographics.pkl')
df_demographics

0              GEO_ID                             NAME  tot_hh  mar_hh   
0    1600000US0800320        Acres Green CDP, Colorado    1040     717  \
1    1600000US0800620      Aetna Estates CDP, Colorado     395     202   
2    1600000US0800760           Aguilar town, Colorado     271      56   
3    1600000US0800870  Air Force Academy CDP, Colorado     643     450   
4    1600000US0800925             Akron town, Colorado     763     345   
..                ...                              ...     ...     ...   
477  1600000US0886117           Woodmoor CDP, Colorado    3224    2633   
478  1600000US0886200        Woody Creek CDP, Colorado      69      42   
479  1600000US0886310              Wray city, Colorado     934     437   
480  1600000US0886475             Yampa town, Colorado     187     103   
481  1600000US0886750              Yuma city, Colorado    1233     606   

0    mar_hh_%  cohabit_hh  cohabit_hh_%  tot_hh_avg_hh_size   
0        68.9          14           1.3                2.63  \
1        51.1           0           0.0                3.18   
2        20.7          32          11.8                1.76   
3        70.0           7           1.1                3.36   
4        45.2          45           5.9                1.99   
..        ...         ...           ...                 ...   
477      81.7         142           4.4                2.74   
478      60.9           0           0.0                1.64   
479      46.8          91           9.7                2.43   
480      55.1           0           0.0                2.39   
481      49.1         115           9.3                2.76   

0    tot_hh_avg_fam_size  pop_in_hh  ...  tot_pop_20-24_%  tot_pop_25-34_%   
0                   3.01       2732  ...              5.7             10.9  \
1                   3.16       1255  ...             10.3             24.9   
2                   2.71        477  ...             10.7              1.7   
3                   3.64       2160  ...             44.2              7.0   
4                   2.50       1521  ...              9.4             13.8   
..                   ...        ...  ...              ...              ...   
477                 2.98       8840  ...              2.5              8.7   
478                 2.05        113  ...              0.0              0.0   
479                 3.20       2272  ...              3.0              9.0   
480                 3.26        447  ...              1.3              9.6   
481                 2.81       3398  ...              8.9             15.9   

0    tot_pop_35-44_%  tot_pop_45-54_%  tot_pop_55-59_%  tot_pop_60-64_%   
0               16.9             13.7              6.3              7.0  \
1                9.6             11.6              4.7              3.7   
2                7.3             14.7              8.4             11.1   
3                6.1              2.9              1.2              0.1   
4               15.3              8.9              4.0              6.3   
..               ...              ...              ...              ...   
477             10.7             13.9             12.0             12.7   
478             44.2              0.0              0.0              9.7   
479             12.5             14.5              6.6              6.8   
480             10.5              8.1              1.1             12.3   
481              7.9              8.3              6.4              7.3   

0    tot_pop_>=21  tot_pop_>=21_%  tot_pop_white_%  tot_pop_hisp_%  
0            2067            75.7             81.3             2.3  
1             878            70.0             49.2            50.6  
2             415            87.0             67.5            67.7  
3            2996            48.6             82.3             9.7  
4            1412            78.8             89.4            15.7  
..            ...             ...              ...             ...  
477          6852            77.5

### Merge Colorado Place Demographics & MSA Places 
* we can use the Pandas dataframe merge method which will retain the geospatial information/column found in a GeoPandas GeoDataFrame even when merged w/ a Pandas dataframe.

In [5]:
def get_select_vars_for_geometry(gdf_geometry, left_merge_col, df_demographics, right_merge_col):
    gdf_place_demographics = pd.merge(
        gdf_geometry, 
        df_demographics, 
        left_on=left_merge_col, 
        right_on=right_merge_col, 
        suffixes=["", "_"])
    
    return gdf_place_demographics
    

gdf_place_demographics = get_select_vars_for_geometry(gdf_msa_places, 'GEO_ID', df_demographics, 'GEO_ID')
os.chdir(
    '/home/jcorley60/Documents/project_portfolio/DenverBreweries/data/US Census Bureau/American Community Survey'
)

# Create several variables from existing columns
gdf_place_demographics['pop_density_>=21'] = (gdf_place_demographics['tot_pop_>=21_%']/100) * gdf_place_demographics['tot_pop'] / gdf_place_demographics['ALAND']

# Create column which sums up % of all desired occupations (by location) which are known to consumer more, on avg
gdf_place_demographics['target_occs_%'] = gdf_place_demographics[
    [col for col in gdf_place_demographics.columns.values if 'occ_>=16' in col and '%' in col]
].sum(axis=1)


# Pickle for later use
gdf_place_demographics.to_pickle('gdf_place_demographics.pkl')
gdf_place_demographics

/home/jcorley60/anaconda3/envs/geospatial/lib/python3.11/site-packages/geopandas/geodataframe.py:1538: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  super().__setitem__(key, value)
/home/jcorley60/anaconda3/envs/geospatial/lib/python3.11/site-packages/geopandas/geodataframe.py:1538: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  super().__setitem__(key, value)


GEO_ID              NAMELSAD     ALAND   AWATER   
0   1600000US0824950             Erie town  53222659   260609  \
1   1600000US0850026  Meridian Village CDP   1319424        0   
2   1600000US0869480      Shaw Heights CDP   1814251     2011   
3   1600000US0852350    Mountain View town    240817        0   
4   1600000US0812815       Centennial city  77035924   379304   
..               ...                   ...       ...      ...   
56  1600000US0816495    Commerce City city  94313381  1035683   
57  1600000US0809280       Broomfield city  85386685  1502572   
58  1600000US0842495         Lakeside town    485965   157267   
59  1600000US0830340         Glendale city   1471186     5724   
60  1600000US0850012          Meridian CDP   6636506        0   

                                             geometry   
0   POLYGON ((-105.10469 40.01455, -105.10380 40.0...  \
1   POLYGON ((-104.83001 39.52793, -104.82992 39.5...   
2   POLYGON ((-105.05042 39.86008, -105.04054 39.8...   
3   POLYGON ((-105.06019 39.77661, -105.05325 39.7...   
4   MULTIPOLYGON (((-104.97913 39.56942, -104.9769...   
..                                                ...   
56  MULTIPOLYGON (((-104.67805 39.91401, -104.6591...   
57  MULTIPOLYGON (((-105.10667 39.95783, -105.1073...   
58  POLYGON ((-105.06266 39.78385, -105.05318 39.7...   
59  POLYGON ((-104.94074 39.70634, -104.94068 39.7...   
60  MULTIPOLYGON (((-104.85366 39.53279, -104.8536...   

                              NAME  tot_hh  mar_hh  mar_hh_%  cohabit_hh  ...   
0              Erie town, Colorado    9879    6889      69.7         387  ...  \
1   Meridian Village CDP, Colorado     980     697      71.1          21  ...   
2       Shaw Heights CDP, Colorado    1681     741      44.1         190  ...   
3     Mountain View town, Colorado     275     138      50.2          22  ...   
4        Centennial city, Colorado   40344   24747      61.3        1913  ...   
..                             ...     ...     ...       ...         ...  ...   
56    Commerce City city, Colorado   19510   11351      58.2        1298  ...   
57       Broomfield city, Colorado   29487   15725      53.3        2165  ...   
58         Lakeside town, Colorado       8       0       0.0           0  ...   
59         Glendale city, Colorado    2692     520      19.3         293  ...   
60          Meridian CDP, Colorado    2564    1028      40.1         225  ...   

    tot_pop_35-44_%  tot_pop_45-54_%  tot_pop_55-59_%  tot_pop_60-64_%   
0              17.7             14.8              6.1              4.9  \
1              19.7             11.7              5.4              7.0   
2              15.7              9.9              4.0              6.6   
3              21.8             13.4              2.8              4.3   
4              14.8             13.6              7.0              7.2   
..              ...              ...              ...              ...   
56             16.3             14.0              4.8              4.0   
57             14.7             14.1              6.4              5.4   
58              0.0              0.0             25.0              0.0   
59             16.2             10.0              3.0              2.4   
60             13.4             13.8              3.0              2.2   

    tot_pop_>=21  tot_pop_>=21_%  tot_pop_white_%  tot_pop_hisp_%   
0          19715            67.1             88.4             9.3  \
1           1846            67.2             72.7             3.3   
2           3801            67.3             66.6            45.3   
3            497            76.7             86.4            27.5   
4          79643            73.8             82.9             9.0   
..           ...             ...              ...             ...   
56         39846            64.8             73.3            48.6   
57         54391            74.8             83.0            12.9   
58             8           100.0            100.0             0.0

# Folium Geospatial Exploration
* https://stackoverflow.com/questions/69170367/python-folium-choropleth-typeerror-ufunc-isnan-not-supported
    - see for assistance w/ determining `key_on` parameter, however, GeoJSON files (often encountered as JSON files) will have a very similar structure from 1 GeoJSON to another
* check GeoJSON structure via
    - d = json.loads(gdf_msa_places.to_json())

#### Map desired variables to specific choropleths w/in Folium

In [7]:
def create_choro_mapping_dict(df):
    """This dictionary maps the category of choropleth (key) to it's corresponding variables (values)
    returns:
    dictionary consisting of choropleth categorical keys and their respective variable values.
    """
    dict_choro_map = dict()

    for col in df.columns.to_list():
        temp_val = df[col][~df[col].isna()].to_list()
        dict_choro_map[col] = temp_val
    
    return dict_choro_map


df_choro_map = pd.read_excel(
    'variableMapping_acs_2021_5yr_data_dictionary.xlsx', 
    sheet_name='organized mapped variables'
)

dict_choro_map = create_choro_mapping_dict(df_choro_map)
dict_choro_map

{'Population': ['tot_pop_>=21',
  'pop_density_>=21',
  'tot_pop',
  'tot_pop_male_%',
  'tot_pop_female_%',
  'tot_pop_20-24_%',
  'tot_pop_25-34_%',
  'tot_pop_35-44_%',
  'tot_pop_45-54_%',
  'tot_pop_55-59_%',
  'tot_pop_60-64_%',
  'tot_pop_white_%',
  'tot_pop_hisp_%',
  'inc_per_capita'],
 'Households': ['tot_hh',
  'tot_housing_units',
  'hhinc_median',
  'hhinc_mean',
  'hhearnings_mean',
  'pop_in_hh',
  'pop_in_hh_%',
  'tot_hh_avg_hh_size',
  'tot_hh_avg_fam_size',
  'mar_hh',
  'mar_hh_%',
  'cohabit_hh',
  'cohabit_hh_%',
  'units_occupied',
  'units_occupied_%',
  'units_vacant',
  'units_vacant_%',
  'homeowner_vacancy_rate',
  'rental_vacancy_rate',
  'units_occupied',
  'units_occupied_%',
  'units_vacant',
  'units_vacant_%',
  'inc_per_capita'],
 'Education': ['edu_attain_>=25',
  'edu_in_college',
  'edu_in_college_%',
  'edu_hs',
  'edu_hs_%',
  'edu_some_col',
  'edu_some_col_%',
  'edu_as',
  'edu_as_%',
  'edu_bs',
  'edu_bs_%',
  'edu_grad_prof',
  'edu_grad_p

In [9]:
# The following code cell comes from:
# https://stackoverflow.com/questions/56164535/adding-colormap-legend-to-folium-map
# Adapted from: https://nbviewer.org/gist/BibMartin/f153aa957ddc5fadc64929abdee9ff2e
from branca.element import MacroElement
from jinja2 import Template


class BindColormap(MacroElement):
    """Binds a colormap to a given layer.

    Parameters
    ----------
    colormap : branca.colormap.ColorMap
        The colormap to bind.
    """
    def __init__(self, layer, colormap):
        super(BindColormap, self).__init__()
        self.layer = layer
        self.colormap = colormap
        self._template = Template(u"""
        {% macro script(this, kwargs) %}
            {{this.colormap.get_name()}}.svg[0][0].style.display = 'block';
            {{this._parent.get_name()}}.on('layeradd', function (eventLayer) {
                if (eventLayer.layer == {{this.layer.get_name()}}) {
                    {{this.colormap.get_name()}}.svg[0][0].style.display = 'block';
                }});
            {{this._parent.get_name()}}.on('layerremove', function (eventLayer) {
                if (eventLayer.layer == {{this.layer.get_name()}}) {
                    {{this.colormap.get_name()}}.svg[0][0].style.display = 'none';
                }});
        {% endmacro %}
        """)  # noqa

In [10]:
def concat_string_to_list(string1, list1):
    """Given a list and a string this function concatenates the string to the beginning of the given list.
    Be sure to generate fresh dictionary after concatenating `NAMELSAD` to avoid runtime issue."""
    list1.insert(0, string1)
    return list1

In [14]:
# TODO: remove the following line of code after this code cell is finalized
dict_choro_map = create_choro_mapping_dict(df_choro_map)

def generate_folium_choropleth(dictionary, gdf):
    """Function to generate choropleth
    
    Category should translate into a choropleth base variable
    """
    base_map = folium.Map(tiles=None, location=[39.755, -104.9], zoom_start=10)
    keys_to_list = list(dictionary.keys())
    
    # Add Layers
    for i in range(len(dictionary)):        
        # create new layer
        if i == 0:
            layer = folium.FeatureGroup(name=keys_to_list[i], overlay=False, control=True, show=True)
        else:
            layer = folium.FeatureGroup(name=keys_to_list[i], overlay=False, control=True, show=False)
        
        # create map for new layer
        folium.TileLayer(
            "OpenStreetMap", 
            location=[39.755, -104.9], 
            zoom_start=10,
            control_scale=True,
        ).add_to(layer)
        layer.add_to(base_map)
         
        # Use built-in color mapping library `cm` which will use the min and max values of given variable
        colorbar = cm.linear.YlOrRd_09.scale(
            gdf_place_demographics[dictionary[keys_to_list[i]][0]].min(), 
            gdf_place_demographics[dictionary[keys_to_list[i]][0]].max()
        )
        colorbar.caption = f'2021 US Census Bureau, ACS 5-Year: {dictionary[keys_to_list[i]][0]}'
        
        folium.Choropleth(
        geo_data=gdf.to_json(), 
        name="choropleth", 
        data=gdf,        # all of our select variables captured in this gdf                   
        columns=("GEO_ID", dictionary[keys_to_list[i]][0]),    # 1st column for category is used
        fill_color="YlOrRd",                # https://r-graph-gallery.com/38-rcolorbrewers-palettes                
        fill_opacity=0.9,
        line_opacity=0.75,
        key_on="feature.properties.GEO_ID",
        ).geojson.add_to(layer)   

        # To get the Place name to show variable `NAMELSAD` must be added
        concat_list = concat_string_to_list('NAMELSAD', dictionary[keys_to_list[i]])
        
        # Add Customized Tooltips to the map
        folium.features.GeoJson(
            data=gdf,
            name='Census Bureau Places',
            smooth_factor=0,
            style_function=lambda x: {'color':'black', 'fillColor':'transparent', 'weight':0.5},
            tooltip=folium.features.GeoJsonTooltip(
                fields=concat_list,
#                 fields=dictionary[keys_to_list[i]],
#                 aliases=[], 
                localize=True,
                sticky=True,
                labels=True,
                style="""
                    background-color: #F0EFEF;
                    border: 2px solid black;
                    border-radius: 3px;
                    box-shadow: 3px;
                    """,),
                highlight_function=lambda x: {'weight':3,'fillColor':'grey'},
                ).add_to(layer)  

        base_map.add_child(colorbar)
        base_map.add_child(BindColormap(layer, colorbar))

    # Add layer control to select different chorpleths
    folium.LayerControl(collapsed=False, position='topright').add_to(base_map)

    # save map to file
    base_map.save("MSA_geographic_demographics.html", close_file=True) 
    
    
    return base_map
    
        
generate_folium_choropleth(dict_choro_map, gdf_place_demographics)

In [12]:
gdf_place_demographics[
    ['tot_pop_>=21', 'tot_hh', 'edu_attain_>=25', 'target_occs_%', 'inc_per_capita', 'target_occs_%']
].describe()

tot_pop_>=21         tot_hh  edu_attain_>=25  target_occs_%   
count      61.000000      61.000000        61.000000      61.000000  \
mean    32092.704918   17118.688525     30000.475410      53.093443   
std     79842.179529   44405.006489     74491.063049       6.618305   
min         8.000000       8.000000         8.000000      22.900000   
25%      2155.000000    1393.000000      2074.000000      50.300000   
50%      7769.000000    3837.000000      7185.000000      53.000000   
75%     26289.000000   13509.000000     24844.000000      56.600000   
max    549933.000000  313926.000000    514105.000000      66.600000   

       inc_per_capita  target_occs_%  
count       61.000000      61.000000  
mean     51334.622951      53.093443  
std      24326.878879       6.618305  
min      13686.000000      22.900000  
25%      35426.000000      50.300000  
50%      49094.000000      53.000000  
75%      56521.000000      56.600000  
max     159642.000000      66.600000

In [13]:
# # https://stackoverflow.com/questions/56164535/adding-colormap-legend-to-folium-map
# # https://nbviewer.org/gist/BibMartin/f153aa957ddc5fadc64929abdee9ff2e
# # https://github.com/python-visualization/folium/issues/399 -- appears closed unresolved

# choro_var = 'tot_pop'

# # Base map: Folium's (aka Leaflet's)`OpenStreetMap`
# base_map = folium.Map(tiles=None, location=[39.757, -104.9], zoom_start=10)

# # Layer 1
# layer_1 = folium.FeatureGroup(name='Total Population', overlay=True, control=True)
# folium.TileLayer(
#     "OpenStreetMap", 
#     location=[39.757, -104.9], 
#     zoom_start=10,
#     control_scale=True,
# ).add_to(layer_1)
# layer_1.add_to(base_map)

# # Layer 2
# layer_2 = folium.FeatureGroup(name='Layer 2', overlay=True, control=True)
# folium.TileLayer(
#     "OpenStreetMap", 
#     location=[39.757, -104.9], 
#     zoom_start=10,
#     control_scale=True,
# ).add_to(layer_2)
# layer_2.add_to(base_map)


# # Use built-in color mapping which uses the min and max values of your data
# colorbar_1 = cm.linear.YlOrRd_09.scale(
#     gdf_place_demographics[choro_var].min(), 
#     gdf_place_demographics[choro_var].max()
# )
# colorbar_1.caption = f'Total Population (2021 US Census Bureau, ACS 5-Year)'

# folium.Choropleth(
#     geo_data=gdf_place_demographics.to_json(), 
#     name="choropleth", 
#     data=gdf_place_demographics,        # all of our select variables captured in this gdf                   
#     columns=("GEO_ID", choro_var),    
#     fill_color="YlOrRd",                # https://r-graph-gallery.com/38-rcolorbrewers-palettes                
#     fill_opacity=0.9,
#     line_opacity=0.75,
#     key_on="feature.properties.GEO_ID",
#     legend_name="Total Population (2021 US Census Bureau, ACS 5-Year)",
# #     threshold_scale=custom_scale
# ).geojson.add_to(layer_1)                                

# # Add Customized Tooltips to the map
# folium.features.GeoJson(
#                     data=gdf_place_demographics,
#                     name='Census Bureau Places',
#                     smooth_factor=0,
#                     style_function=lambda x: {'color':'black', 'fillColor':'transparent', 'weight':0.5},
#                     tooltip=folium.features.GeoJsonTooltip(
#                         fields=['NAMELSAD',
#                                 'tot_pop',
#                                 'inc_per_capita',
#                                 'tot_pop_male_%',
#                                 'tot_pop_female_%',
#                                 'tot_pop_>=21_%',
#                                 'tot_pop_white_%',
#                                 'tot_pop_hisp_%',
#                                ],
#                         aliases=["Place:",
#                                  "Total Population:",
#                                  "Income Per Capita ($):",
#                                  "Population, male (% of total):",
#                                  "Population, female (% of total):",
#                                  "Total Population >= 21 y.o. (% of total):",
#                                  "Total Population, white (% of total):",
#                                  "Total Population, hispanic of any race (% of total):"
#                                 ], 
#                         localize=True,
#                         sticky=True,
#                         labels=True,
#                         style="""
#                             background-color: #F0EFEF;
#                             border: 2px solid black;
#                             border-radius: 3px;
#                             box-shadow: 3px;
#                         """,),
#                             highlight_function=lambda x: {'weight':3,'fillColor':'grey'},
#                         ).add_to(layer_1)  

# base_map.add_child(colorbar_1)
# base_map.add_child(BindColormap(layer_1, colorbar_1))

# folium.LayerControl(collapsed=False, position='topright').add_to(base_map)

# # save map to file
# # base_map.save("MSA_index.html", close_file=True) 

# base_map